# Hvordan optimere kode med Numba og `@jit`

Første bud for all optimering:
**Skriv først kode som virker!** Ikke tenk på ytelsen, bare gjør ting så rett frem som mulig og kjør tester med lite belastning. Deretter kan du gjøre det raskere hvis det absolutt er nødvendig (ofte er det ikke det). Når du modifiserer en funksjon for å få den raskere, sjekk resultatene fortløpende mot den trege versjonen som du vet stemmer.

Når det kommer til Numba betyr dette at du **ikke** slenger på `@jit` uten at du først er **sikker på** at funksjonen fungerer og at den går for sakte.

Før du bruker Numba, les igjennom dette dokumentet samt Numba-delen av det numeriske kompendiet: /studier/emner/matnat/astro/AST2000/h18/undervisningsmateriell_h2018/Numerical%20Compendium/numba.pdf

Det vil sannsynligvis ta deg mindre tid enn å løse feilene som typisk oppstår ved å ikke gjøre det.

## Bruk `@jit` på trege funksjoner med arrayer og løkker

In [ ]:
import numpy as np
import numba as nb
from numba import jit

Her er en Python-funksjon med mye beregning, som bare bruker enkle objekter som arrayer og skalarer.

In [ ]:
def fibonacci(N):
    """
    Computes the Fibonacci sequence with N elements.
    """
    assert N >= 2, 'N cannot be smaller than 2'
    a = np.zeros(N)
    a[1] = 1.0
    for i in range(2, N):
        a[i] = a[i-1] + a[i-2]
    return a

Vi kan måle tiden den bruker på å regne ut de 1000 første tallene i Fibonacci-følgen.

In [ ]:
%timeit fibonacci(1000)

Men hva hvis vi trenger å gjøre dette raskere?

`fibonacci` er et godt eksempel på en funksjon som egner seg til å gjøres raskere med Numba. Ved å sette inn `@jit(nopython=True)` over funksjonen, kan vi be Numba gjøre om hele funksjonen til effektiv maskinkode rett før den skal kalles. JIT står for "Just-In-Time compilation".

In [ ]:
@jit(nopython=True)
def fibonacci_jit(N):
    """
    Computes the Fibonacci sequence with N elements.
    """
    assert N >= 2, 'N cannot be smaller than 2'
    a = np.zeros(N)
    a[1] = 1.0
    for i in range(2, N):
        a[i] = a[i-1] + a[i-2]
    return a

In [ ]:
%timeit fibonacci_jit(1000) # ~150 times faster than fibonacci

## Unngå `@jit` på raske funksjoner

Merk at `@jit` ikke bør brukes på funksjoner som allerede går raskt nok. De kan fort vise seg å bli treigere grunnet tiden det tar å konvertere til maskinkode. Å legge til `@jit` innebærer også en viss risiko (som vi skal se), så ikke gjør det med mindre det er nødvendig.

In [ ]:
def fibonacci_cheat(N):
    """
    Returns the Fibonacci sequence with N=5 elements.
    """
    assert N == 5, 'N must be 5'
    return np.array([0.0, 1.0, 1.0, 2.0, 3.0])

In [ ]:
%timeit -r1 -n1 fibonacci_cheat(5)

In [ ]:
@jit(nopython=True)
def fibonacci_cheat_jit(N):
    """
    Returns the Fibonacci sequence with N=5 elements.
    """
    assert N == 5, 'N must be 5'
    return np.array([0.0, 1.0, 1.0, 2.0, 3.0])

In [ ]:
%timeit -r1 -n1 fibonacci_cheat_jit(5) # ~50 000 times slower than fibonacci_cheat for first call!

## `@jit` har mindre effekt med mer kompliserte datastrukturer

`@jit` fungerer best når funksjonen (og alle funksjoner som kalles inni) kun bruker arrayer og skalarer til å håndtere data, siden de har en fast lengde og kan representeres enkelt på maskinnivå. Lister, for eksempel, er mer kompliserte siden de ikke har en forhåndsdefinert lengde.

Følgende variant av `fibonacci` lagrer verdiene i en liste istendefor en array.

In [ ]:
def fibonacci_list(N):
    """
    Computes the Fibonacci sequence with N elements.
    Grows a list instead of inserting into an array.
    """
    assert N >= 2, 'N cannot be smaller than 2'
    a = [0.0, 1.0]
    for i in range(2, N):
        a.append(a[i-1] + a[i-2])
    return a

In [ ]:
%timeit fibonacci_list(1000)

In [ ]:
@jit(nopython=True)
def fibonacci_list_jit(N):
    """
    Computes the Fibonacci sequence with N elements.
    Grows a list instead of inserting into an array.
    """
    assert N >= 2, 'N cannot be smaller than 2'
    a = [0.0, 1.0]
    for i in range(2, N):
        a.append(a[i-1] + a[i-2])
    return a

Den `@jit`ede versjonen går litt raskere, men ikke så veldig mye.

In [ ]:
%timeit fibonacci_list_jit(1000) # ~7 times faster than fibonacci_list

Med `@jit(nopython=True)` kan du fort få en feilmelding hvis funksjonen din benytter for kompliserte datastrukturer, som for eksempel dictionaries. `nopython=True` betyr at all koden i funksjonen skal oversettes til rask maskinkode, slik at Python selv kan lene seg tilbake og la maskinen overta når funksjonen kalles. Men kompliserte datastrukturer kan som regel ikke oversettes på denne måten. Med `nopython=True` vil derimot Python selv ta hånd om de delene av funksjonen som ikke kan oversettes direkte, men dette vil typisk gå mye saktere.

Her er en variant av `fibonacci` lagrer verdiene i en `dict` istedenfor en array.

In [ ]:
def fibonacci_dict(N):
    """
    Computes the Fibonacci sequence with N elements.
    Builds a dictionary instead of inserting into an array.
    (This is a very stupid way of using a dictionary..)
    """
    assert N >= 2, 'N cannot be smaller than 2'
    a = {0: 0.0, 1: 1.0}
    for i in range(2, N):
        a[i] = a[i-1] + a[i-2]
    return a

In [ ]:
%timeit fibonacci_dict(1000)

In [ ]:
@jit(nopython=True)
def fibonacci_dict_jit(N):
    """
    Computes the Fibonacci sequence with N elements.
    Builds a dictionary instead of inserting into an array.
    (This is a very stupid way of using a dictionary..)
    """
    assert N >= 2, 'N cannot be smaller than 2'
    a = {0: 0.0, 1: 1.0}
    for i in range(2, N):
        a[i] = a[i-1] + a[i-2]
    return a

Med `nopython=True` nekter Numba å lystre, siden den ikke vet hvordan man oversetter dictionaries.

In [ ]:
try:
    fibonacci_dict_jit(1000) # UnsupportedError: Failed in nopython mode pipeline
except nb.UnsupportedError as e:
    print(e)

Vi kan istedenfor prøve å sette `nopython=False`.

In [ ]:
@jit(nopython=False)
def fibonacci_dict_jit_python(N):
    """
    Computes the Fibonacci sequence with N elements.
    Builds a dictionary instead of inserting into an array.
    (This is a very stupid way of using a dictionary..)
    """
    assert N >= 2, 'N cannot be smaller than 2'
    a = {0: 0.0, 1: 1.0}
    for i in range(2, N):
        a[i] = a[i-1] + a[i-2]
    return a

Nå vil funksjonen kjøre, men den går ikke raskere enn den gamle versjonen siden `dict`-objektet er en sentral del av utregningene.

In [ ]:
%timeit fibonacci_dict_jit_python(1000) # Slightly slower than fibonacci_dict

## `@jit` på funksjoner med bugs kan ha katastrofale konsekvenser

Husk at du **alltid** må teste at funksjonen din fungerer som den skal **før** du bruker `@jit` på den. Dette gjelder også hver gang du endrer noe i funksjonen senere, **kommenter ut `@jit` hver gang du modifiserer funksjonen og ikke aktiver det igjen før du vet at ting fungerer!**

Det er i prinsippet ikke noe problem å endre ting mens funksjonen er `@jit`et, neste gang den kalles vil den oversettes på nytt og endringene vil tre i kraft. Problemet er at `@jit`et kode kan gi kryptiske feilmeldinger som følge av problemer som ikke egentlig har noe med `@jit` å gjøre i det hele tatt, eller enda verre, la være å gi feilmeldinger selv om ting går galt!

Et skrekkeksempel på dette kan du se her.

In [ ]:
def fibonacci_buggy(N):
    """
    Computes the Fibonacci sequence with N elements.
    WARNING: THIS CODE HAS A MISTAKE!
    """
    assert N >= 2, 'N cannot be smaller than 2'
    a = np.zeros(N)
    a[1] = 1.0
    for i in range(2, N+1): # Whoops, should be range(2, N)
        a[i] = a[i-1] + a[i-2]
    return a

I `fibonacci_buggy` har den øvre grensen i `for`-løkken ved en feiltagelse blitt satt til `N+1` istedenfor `N`. Dette medfører at koden vil prøve å skrive til `a[N]` i siste iterasjon, som er ugyldig siden siste element i arrayen er `a[N-1]`. Men dette sier heldigvis Python tydelig ifra om.

In [ ]:
try:
    print(fibonacci_buggy(5)) # Saved by bounds check
except IndexError as e:
    print(e)

Men hvordan går dette i den `@jit`ede versjonen?

In [ ]:
@jit(nopython=True)
def fibonacci_buggy_jit(N):
    """
    Computes the Fibonacci sequence with N elements.
    WARNING: THIS CODE HAS A MISTAKE!
    """
    assert N >= 2, 'N cannot be smaller than 2'
    a = np.zeros(N)
    a[1] = 1.0
    for i in range(2, N+1): # Whoops, should be range(2, N)
        a[i] = a[i-1] + a[i-2]
    return a

In [ ]:
try:
    print(fibonacci_buggy_jit(5)) # Uh oh, anything can happen now
except IndexError as e:
    print(e)

Ingen feilmelding.. Men det betyr at koden fikk lov å skrive utenfor arrayen. Dette virker kanskje uskyldig nok, men tenk på hva det innebærer. Hva som helst av informasjon som programmet benytter til å kjøre kan ha vært lagret på minneadressen som vi akkurat overskrev, det være seg kodeinstrukser eller variabler. Det betyr at det ikke er noen måte å forutse hva programmet vil finne på! Og utfallet vil variere med tiden, månefasen og hva du lytter til på Spotify. Vi har støtt på enhver feilsøkers verste mareritt: **udefinert oppførsel**!

Moralen er at `@jit` skal holdes langt unna kode som du ikke først har testet at fungerer. Og hvis du mistenker at noe er galt bør det første du gjør være å fjerne `@jit` før du feilsøker.

## Andre fallgruver

### Kalle funksjoner som er definert uten `@jit`

In [ ]:
def fibonacci_nested(N):
    return fibonacci(N) # fibonacci is not @jit'ed

In [ ]:
print(fibonacci_nested(5))

In [ ]:
@jit(nopython=True)
def fibonacci_nested_jit(N):
    return fibonacci(N) # fibonacci is not @jit'ed

In [ ]:
try:
    print(fibonacci_nested_jit(5)) # TypingError: Failed in nopython mode pipeline
except nb.TypingError as e:
    print(e)

In [ ]:
@jit(nopython=True)
def fibonacci_nested_jit_working(N):
    return fibonacci_jit(N) # fibonacci_jit is @jit'ed

In [ ]:
print(fibonacci_nested_jit_working(5))

### Definere en variabel flere ganger

In [ ]:
def fibonacci_redefine(N):
    """
    Computes the Fibonacci sequence with N elements.
    The array is first defined as a list and then converted into an array.
    """
    assert N >= 2, 'N cannot be smaller than 2'
    a = [0.0]*N
    a = np.array(a) # Variable a is redefined
    a[1] = 1.0
    for i in range(2, N):
        a[i] = a[i-1] + a[i-2]
    return a

In [ ]:
print(fibonacci_redefine(5))

In [ ]:
@jit(nopython=True)
def fibonacci_redefine_jit(N):
    """
    Computes the Fibonacci sequence with N elements.
    The array is first defined as a list and then converted into an array.
    """
    assert N >= 2, 'N cannot be smaller than 2'
    a = [0.0]*N
    a = np.array(a) # Variable a is redefined
    a[1] = 1.0
    for i in range(2, N):
        a[i] = a[i-1] + a[i-2]
    return a

In [ ]:
try:
    print(fibonacci_redefine_jit(5)) # TypingError: Failed in nopython mode pipeline
except nb.TypingError as e:
    print(e)

### Sende inn en funksjon som argument

In [ ]:
def fibonacci_custom_operator(N, operation):
    """
    Computes the Fibonacci sequence with N elements.
    The argument `operation` is a function that combines two numbers into one.
    """
    assert N >= 2, 'N cannot be smaller than 2'
    a = np.zeros(N)
    a[1] = 1.0
    for i in range(2, N):
        a[i] = operation(a[i-1], a[i-2]) # Uses inputted function to combine elements
    return a

In [ ]:
print(fibonacci_custom_operator(5, lambda a, b: a + b))

In [ ]:
@jit(nopython=True)
def fibonacci_custom_operator_jit(N, operation):
    """
    Computes the Fibonacci sequence with N elements.
    The argument `operation` is a function that combines two numbers into one.
    """
    assert N >= 2, 'N cannot be smaller than 2'
    a = np.zeros(N)
    a[1] = 1.0
    for i in range(2, N):
        a[i] = operation(a[i-1], a[i-2]) # Uses inputted function to combine elements
    return a

In [ ]:
try:
    print(fibonacci_custom_operator_jit(5, lambda a, b: a + b)) # TypingError: Failed in nopython mode pipeline
except nb.TypingError as e:
    print(e)